In [13]:
import pandas as pd
import numpy as np
import plotly
#import plotly.plotly as py
import  plotly.offline  as py
import plotly.graph_objs as go
from plotly import tools
import plotly.graph_objs as graph_objs
import json
import os
from mapboxgl.viz import *
from mapboxgl.utils import *
from colour import Color
import os
import urllib.request, json 

%matplotlib inline
py.init_notebook_mode(connected=True)
mapbox_access_token=os.environ['MAPBOX_ACCESS_TOKEN']

In [14]:
ds = pd.read_excel('evolution.xls')
# Use the department code as index
ds = ds.rename(columns={
    'Variation des effectifs par qualification depuis 2010 - DERMATOLOGIE ET VENEREOLOGIE - 2010_2018 (%)': 'dermato',
    'Variation des effectifs par qualification depuis 2010 - GYNECOLOGIE MEDICALE - 2010_2018 (%)': 'gyneco',
    'Variation des effectifs par qualification depuis 2010 - MEDECINE GENERALE - 2010_2018 (%)': 'generalists',
    'Variation des effectifs par qualification depuis 2010 - PEDIATRIE - 2010_2018 (%)': 'pediatre',
    'Département': 'departement',
    'Code': 'code'
})
ds = ds.set_index('departement')
ds['gyneco'] = ds['gyneco'].replace('N/A - division par 0', np.nan)
ds[['gyneco', 'dermato', 'generalists', 'pediatre']] = ds[['gyneco', 'dermato', 'generalists', 'pediatre']].apply(pd.to_numeric)
ds.info()

<class 'pandas.core.frame.DataFrame'>
Index: 102 entries, Ain to Étranger
Data columns (total 5 columns):
code           102 non-null object
dermato        101 non-null float64
gyneco         96 non-null float64
generalists    102 non-null float64
pediatre       102 non-null float64
dtypes: float64(4), object(1)
memory usage: 4.8+ KB


In [15]:
# Geo data from Github Public API
with urllib.request.urlopen("https://raw.githubusercontent.com/gregoiredavid/france-geojson/master/departements-version-simplifiee.geojson") as url:
    geodata = json.loads(url.read().decode())
sources=[]
print(geodata['features'][0]['properties'])

# Create new geojson with evolution data
for feat in geodata['features']:
    for job, value in zip(ds.loc[feat['properties']['nom']].index, ds.loc[feat['properties']['nom']]):
        feat['properties'][job] = value
print(geodata['features'][0]['properties'])

with open('export.geojson', 'w') as fh:
    a = json.dump(geodata, fh)

{'code': '01', 'nom': 'Ain'}
{'gyneco': -66.700000000000003, 'nom': 'Ain', 'generalists': -5.9000000000000004, 'code': '01', 'dermato': -37.5, 'pediatre': 0.0}


In [16]:
def build_palettes(ds):
    red = Color('red')
    yellow = Color('yellow')
    green = Color('green')
    palettes = dict()
    for job in ds.columns[1:]:
        palettes[job] = list(red.range_to(yellow, len(set(ds[ds[job] <= 0][job])))) + list(yellow.range_to(green, len(set(ds[ds[job] > 0][job]))))
        palettes[job].remove(Color('yellow'))
        if ds[job].isnull().any():
            palettes[job].append(Color('white'))
        print(len(palettes[job]))
    return palettes

palettes = build_palettes(ds)

def find_color(properties, job):
    if np.isnan(properties[job]):
        return '#ffffff'
    unique_values = list(ds[job].sort_values().unique())
    target_index = unique_values.index(properties[job])
    return palettes[job][target_index].hex

69
48
84
81


In [17]:
def get_coords(geometry):
    lats = []
    lonts = []
    for item in geometry['coordinates']:
        for coords in item:
            lont = []
            lat = []
            if len(coords) != 2:
                for tmp in coords:
                    lont.append(tmp[0])
                    lat.append(tmp[1])
            else:
                lont.append(coords[0])
                lat.append(coords[1])
            lats += lat
            lonts += lont
    return lats, lonts

In [18]:
tmp_job = 'generalists'
departs = []
for index, job in enumerate(ds.columns[1:]):
    for layer in geodata['features']:
        new_item = go.Scattermapbox(
            mode='lines',
            legendgroup= 'group' if index < 2 else 'group2', 
            line=dict(
                width=1,
                color='black'
            ),
            marker=dict(
                size=1
            ),
            fill='toself',
            name=layer['properties']['nom'],
            hoverinfo="text",
            hovertext='{name}: {evolution}%'.format(name=layer['properties']['nom'], evolution=str(layer['properties'][job])),
            hoverlabel=dict(
                bgcolor='white'
            ),
            subplot='mapbox{nb}'.format(nb=index+1 if index != 0 else '')
        )
        new_item['fillcolor'] = find_color(layer['properties'], job)
        lats, lonts = get_coords(layer['geometry'])
        new_item['lat'] = lats
        new_item['lon'] = lonts
        departs.append(new_item)

In [19]:
data = departs

zoom_value = 4.7
layout = go.Layout(
    height=700,
    autosize=True,
    showlegend=False,
    hovermode='closest',
    annotations=[
        dict(
            x=0.20,
            y=0.5,
            showarrow=False,
            text='Médecins généralistes',
            xref='paper',
            yref='paper',
            font=dict(
                size=15
            ),
            align='center'
        ),
        dict(
            x=0.20,
            y=-0.05,
            showarrow=False,
            text='Dermatologues',
            xref='paper',
            yref='paper',
            font=dict(
                size=15
            ),
            align='center'
        ),
        dict(
            x=0.80,
            y=0.5,
            showarrow=False,
            text='Pédiatres',
            xref='paper',
            yref='paper',
            font=dict(
                size=15
            ),
            align='center'
        ),
        dict(
            x=0.85,
            y=-0.05,
            showarrow=False,
            text='Gynécologues médicaux',
            xref='paper',
            yref='paper',
            font=dict(
                size=15
            ),
            align='center'
        )],
    mapbox=dict(
        #layers=layers,
        accesstoken=mapbox_access_token,
        domain={'x': [0, 0.5], 'y': [0, 0.48]},
        bearing=0,
        center=dict(
            lat=46.5,
            lon=2.32
        ),
        pitch=0,
        zoom=zoom_value,
    ),
    mapbox2=dict(
        #layers=layers,
        domain={'x': [0.5, 1], 'y': [0, 0.48]},
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=46.5,
            lon=2.32
        ),
        pitch=0,
        zoom=zoom_value,
    ),
    mapbox3=dict(
        #layers=layers,
        domain={'x': [0, 0.5], 'y': [0.52, 1]},
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=46.5,
            lon=2.32
        ),
        pitch=0,
        zoom=zoom_value,
    ),
    mapbox4=dict(
        #layers=layers,
        domain={'x': [0.5, 1], 'y': [0.52, 1]},
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=46.5,
            lon=2.32
        ),
        pitch=0,
        zoom=zoom_value,
    ),
    title='Évolution du nombre de praticiens pour 100 000 habitants depuis 2010 par département, en %'
)

fig = dict(data=data, layout=layout)
py.iplot(fig, filename='county-level-choropleths-python')